In [1]:
import os
import pandas as pd
import geopandas as gpd
import getpass
from mappymatch import package_root
from mappymatch.constructs.trace import Trace
from mappymatch.utils.plot import plot_trace
from mappymatch.utils.plot import plot_geofence
from mappymatch.constructs.geofence import Geofence
from mappymatch.maps.nx.nx_map import NxMap, NetworkType
from mappymatch.utils.plot import plot_map
from mappymatch.matchers.lcss.lcss import LCSSMatcher
from mappymatch.utils.plot import plot_matches
from mappymatch.utils.plot import plot_path

user = getpass.getuser().lower()


# !pip install mappymatch

## Define functions

In [2]:
# create a batch process function to create a list of traces

def create_batch_traces(df, unique_ids, xy=True):
    """Create a batch of traces from a dataframe with xy coordinates

    Args:
        df (Pandas Dataframe): Dataframe with xy coordinates in EPGS:4326
        unique_ids (List): List of unique trip ids
        xy (bool, optional): Projects trace to EPSG:3857. Defaults to True.

    Returns:
        List: List of traces
    """
    batch_traces = []
    for i in unique_ids:
        filter_df = df[df["trip_id"] == i]
        gdf = gpd.GeoDataFrame(
            filter_df, geometry=gpd.points_from_xy(filter_df.lon, filter_df.lat), crs=4326
        )
        batch_trace = Trace.from_geo_dataframe(frame=gdf, xy=xy)
        batch_traces.append(batch_trace)
    return batch_traces

## Prepare the data

In [3]:
## Define file name
location_tbl = 'location.csv'
trip_tbl = 'trip.csv'

## Define Box System Root Directory
box_dir = os.path.join(
    "/Users", user, "Library", "CloudStorage", "Box-Box"
    )

## Define BAUS directory on Box for .csv output files
file_dir = os.path.join(
    box_dir, "Modeling and Surveys", "Surveys", "Travel Diary Survey",
    "Biennial Travel Diary Survey", "Data",'2023', "Full Unweighted 2023 Dataset"
)

location_path = os.path.join(file_dir, location_tbl)
trip_path = os.path.join(file_dir, trip_tbl)

In [4]:
# read location and trip 
location_df = pd.read_csv(location_path)
trip_df = pd.read_csv(trip_path)

In [5]:
# merge trips with locations
trip_locations = pd.merge(
    location_df,
    trip_df[
        [
            "trip_id",
            "o_in_region",
            "d_in_region",
            "mode_type",
            "mode_1",
            "mode_2",
            "mode_3",
            "mode_4",
        ]
    ],
    on="trip_id",
)

In [6]:
trip_locations.head()

trip_id          collect_time  accuracy  bearing  speed       lat  \
0  2333407402022  2023-11-02T00:23:43Z      13.0    120.0    4.0  37.85270   
1  2333407402022  2023-11-02T00:23:50Z       8.0    175.0    4.0  37.85227   
2  2333407402022  2023-11-02T00:24:04Z      12.0    185.0    4.0  37.85163   
3  2333407402022  2023-11-02T00:24:23Z       8.0    129.0    4.0  37.85092   
4  2333407402022  2023-11-02T00:24:49Z      11.0     73.0    4.0  37.85138   

         lon  o_in_region  d_in_region  mode_type  mode_1  mode_2  mode_3  \
0 -122.21255            1            1          2       2     995     995   
1 -122.21236            1            1          2       2     995     995   
2 -122.21239            1            1          2       2     995     995   
3 -122.21197            1            1          2       2     995     995   
4 -122.21071            1            1          2       2     995     995   

   mode_4  
0     995  
1     995  
2     995  
3     995  
4     995

In [7]:
# filter trips_locations to only include trips with mode 8 (car) with origins and destinations in region
car_trips = trip_locations[
    (trip_locations["mode_type"] == 8)
    & (trip_locations["o_in_region"] == 1)
    & (trip_locations["d_in_region"] == 1)
]

In [8]:
# create unique trip ids list
unique_ids = car_trips.trip_id.unique()

In [9]:
unique_ids[10]

2333407402037

In [10]:
# car_trips[car_trips["trip_id"] ==2333407402037]

In [11]:
test_list = [
    2304076901001, #highway
    2333407402028, #highway
    2304076901002, #highway
    2347455701047, #highway
    # 2333407402031, #might be too long
    2333407402037,
]

In [12]:
# create batch traces
batch_traces = create_batch_traces(car_trips, test_list, xy=True)

## Explore using the LCSS Matcher

In [13]:
plot_trace(batch_traces[3], point_color="black", line_color="yellow")

In [14]:
geofence = Geofence.from_trace(batch_traces[3], padding=1e3)


In [15]:
plot_trace(batch_traces[3], point_color="black", m=plot_geofence(geofence))


In [16]:
nx_map = NxMap.from_geofence(geofence, network_type=NetworkType.DRIVE)

In [17]:
plot_map(nx_map)

In [18]:
matcher = LCSSMatcher(nx_map)
match_result = matcher.match_trace(batch_traces[3])

In [19]:
plot_matches(match_result.matches)

In [20]:
plot_trace(batch_traces[3], point_color="blue", m=plot_path(match_result.path, crs=3857))

In [21]:
# plot_trace(reduced_trace, point_color="blue", m=plot_path(reduced_matches.path, crs=trace.crs))

In [22]:
result_df = match_result.matches_to_dataframe()
result_df

coordinate_id  distance_to_road                      road_id  \
0         1752492         37.131890     (65395388, 276566344, 0)   
1         1752493          3.768171    (415168199, 415168195, 0)   
2         1752494          0.584147    (415168199, 415168195, 0)   
3         1752495          4.563891    (415168199, 415168195, 0)   
4         1752496          5.632155    (415168195, 415168193, 0)   
5         1752497          2.873897    (415168193, 415168189, 0)   
6         1752498          0.063217    (415168189, 415168187, 0)   
7         1752499         11.287881     (415168390, 65417685, 0)   
8         1752500          1.112094     (65417685, 276571753, 0)   
9         1752501          2.488833     (65417685, 276571753, 0)   
10        1752502          4.202162     (276571753, 65492836, 0)   
11        1752503          0.489929    (65471603, 1642836834, 0)   
12        1752504         10.853155      (65377236, 65353467, 0)   
13        1752505         25.672470      (65377236, 65353467, 0)   
14        1752506         76.453813      (65377236, 65353467, 0)   
15        1752507        114.111280      (65377236, 65353467, 0)   
16        1752508        109.797294      (65377236, 65353467, 0)   
17        1752509         62.368635      (65358295, 65377236, 0)   
18        1752510         14.602800    (564663743, 437194911, 0)   
19        1752511          2.140944     (437194911, 65367771, 0)   
20        1752512          4.797974     (65367771, 428765474, 0)   
21        1752513          6.144534      (65485287, 65381925, 0)   
22        1752514          2.391652      (65358806, 65355466, 0)   
23        1752515          7.274654      (65358806, 65355466, 0)   
24        1752516          5.972735      (65355466, 65485312, 0)   
25        1752517          5.708324      (65485312, 69835800, 0)   
26        1752518          6.680086      (65348550, 65372919, 0)   
27        1752519          8.255627      (65382289, 65828370, 0)   
28        1752520          6.319252      (65405009, 65400935, 0)   
29        1752521          5.824876      (65405009, 65400935, 0)   
30        1752522          7.126145      (65382597, 65593180, 0)   
31        1752523          3.243273      (65392096, 65389683, 0)   
32        1752524          7.657888    (65386032, 1350115374, 0)   
33        1752525          3.783968     (65393813, 447920760, 0)   
34        1752526          4.500691    (65417858, 1970807537, 0)   
35        1752527          7.641113     (65415279, 257881189, 0)   
36        1752528          4.831152   (257881189, 2185799705, 0)   
37        1752529          5.035575   (257881189, 2185799705, 0)   
38        1752530          5.403992     (33106555, 667714607, 0)   
39        1752531          6.817869    (297690759, 258968455, 0)   
40        1752532          5.292977     (258968455, 33106550, 0)   
41        1752533          5.470940  (1126243283, 1126243341, 0)   
42        1752534         18.013325      (65530571, 65535694, 0)   
43        1752535        154.958488      (65530571, 65535694, 0)   

                                                 geom  origin_junction_id  \
0   LINESTRING (-13611261.420297913 4515868.669849...            65395388   
1   LINESTRING (-13611454.926968759 4515764.081350...           415168199   
2   LINESTRING (-13611454.926968759 4515764.081350...           415168199   
3   LINESTRING (-13611454.926968759 4515764.081350...           415168199   
4   LINESTRING (-13611526.204838712 4516025.013984...           415168195   
5   LINESTRING (-13611529.611215131 4516150.540287...           415168193   
6   LINESTRING (-13611675.43974807 4516433.0220988...           415168189   
7   LINESTRING (-13611860.575193208 4516676.461318...           415168390   
8   LINESTRING (-13611875.825963447 4516664.216908...            65417685   
9   LINESTRING (-13611875.825963447 4516664.216908...            65417685   
10  LINESTRING (-13612193.498394324 4516345.193280...           276571753   
11  LINESTRING (-13

In [23]:
gpd.GeoDataFrame(result_df, geometry='geom', crs="EPSG:3857").explore()


## Explore the OSRM Matcher

In [24]:
from mappymatch.matchers.osrm import OsrmMatcher

In [25]:
matcher = OsrmMatcher()

In [26]:
# create batch traces in 4326
batch_traces_4326 = create_batch_traces(car_trips, test_list, xy=False)

In [27]:
plot_trace(batch_traces_4326[0], line_color="yellow", point_color="black")

In [28]:
match_result = matcher.match_trace(batch_traces_4326[0])

http://router.project-osrm.org/match/v1/driving/-121.8519,37.9987;-121.85392,37.99996;-121.8533,38.0012;-121.85353,38.00147;-121.85437,38.00166;-121.85568,38.00232;-121.85541,38.00301;-121.85454,38.00435;-121.85369,38.0049;-121.8541,38.00599;-121.85542,38.00798;-121.85399,38.01003;-121.85445,38.01043;-121.85577,38.01085;-121.85698,38.01097;-121.85713,38.01065;-121.85854,38.01003;-121.8653,38.01196;-121.86808,38.0131;-121.86945,38.01273;-121.8742,38.01354;-121.88972,38.01718;-121.898,38.01936;-121.90157,38.01998;-121.90538,38.02016;-121.91984,38.02025;-121.92205,38.02008;-121.92846,38.01918;-121.9476,38.01911;-121.94922,38.01935;-121.95423,38.02082;-121.95642,38.02131;-121.97075,38.02392;-121.97276,38.02398;-121.97637,38.0235;-121.97814,38.02296;-121.98838,38.01853;-121.99425,38.01514;-121.99601,38.01438;-121.99805,38.01376;-122.00191,38.01306;-122.02333,38.00986;-122.03508,38.00689;-122.03841,37.99815;-122.04168,37.98294;-122.04215,37.98142;-122.04765,37.97111;-122.04859,37.96747;-122.

In [29]:
match_result.matches

[Match(road=Road(road_id=RoadId(start='348529033', end='348529033', key=0), geom=None, metadata=None), coordinate=Coordinate(coordinate_id=280, x=-121.8519, y=37.9987, crs=('EPSG', '4326')), distance=inf),
 Match(road=Road(road_id=RoadId(start='57885949', end='57885949', key=0), geom=None, metadata=None), coordinate=Coordinate(coordinate_id=281, x=-121.85392, y=37.99996, crs=('EPSG', '4326')), distance=inf),
 Match(road=Road(road_id=RoadId(start='57931331', end='57931331', key=0), geom=None, metadata=None), coordinate=Coordinate(coordinate_id=282, x=-121.8533, y=38.0012, crs=('EPSG', '4326')), distance=inf),
 Match(road=Road(road_id=RoadId(start='2565663167', end='2565663167', key=0), geom=None, metadata=None), coordinate=Coordinate(coordinate_id=283, x=-121.85353, y=38.00147, crs=('EPSG', '4326')), distance=inf),
 Match(road=Road(road_id=RoadId(start='2565663167', end='2565663167', key=0), geom=None, metadata=None), coordinate=Coordinate(coordinate_id=284, x=-121.85437, y=38.00166, cr

In [30]:
# no geometry :( 

In [31]:
# plot_trace(trace, point_color="blue", m=plot_path(match_result.path, crs=3857))

## Explore using the Valhalla Matcher

In [32]:
from mappymatch.matchers.valhalla import ValhallaMatcher

In [33]:
matcher = ValhallaMatcher(attributes={'edge.length', 'edge.speed', 'edge.names', 'edge.road_class'})

In [34]:
# trace = Trace.from_geo_dataframe(gdf, xy=False)

In [35]:
match_result = matcher.match_trace_batch(batch_traces)

In [36]:
# match_result[9]

In [37]:
plot_matches(match_result[0].matches, crs="EPSG:4326")

In [38]:
plot_trace(batch_traces[0], point_color="blue", m=plot_path(match_result[0].path, crs="EPSG:4326"))

In [39]:
plot_matches(match_result[2].matches, crs="EPSG:4326")

In [40]:
plot_trace(batch_traces[2], point_color="blue", m=plot_path(match_result[2].path, crs="EPSG:4326"))

In [41]:
plot_matches(match_result[3].matches, crs="EPSG:4326")

In [42]:
plot_trace(batch_traces[3], point_color="blue", m=plot_path(match_result[3].path, crs="EPSG:4326"))

In [43]:
plot_matches(match_result[4].matches, crs="EPSG:4326")

In [44]:
plot_trace(batch_traces[4], point_color="blue", m=plot_path(match_result[4].path, crs="EPSG:4326"))